In [11]:
import pickle
from music21 import *

In [3]:
import torch
import torch.nn as nn
from torch.nn import functional as F

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

class GenerationRNN(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, n_layers=1):
        super(GenerationRNN, self).__init__()
        self.input_size = input_size
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.n_layers = n_layers
        
        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size, n_layers)
        self.decoder = nn.Linear(hidden_size * n_layers, output_size)
    
    def forward(self, input, hidden):
        # Creates embedding of the input texts
        #print('initial input', input.size())
        input = self.embedding(input.view(1, -1))
        #print('input after embedding', input.size())
        output, hidden = self.gru(input, hidden)
        #print('output after gru', output.size())
        #print('hidden after gru', hidden.size())
        output = self.decoder(hidden.view(1, -1))
        #print('output after decoder', output.size())
        return output, hidden

    def init_hidden(self):
        return torch.zeros(self.n_layers, 1, self.hidden_size).to(device)

In [4]:
def predict_multimomial(net, prime_seq, predict_len, temperature=0.8):
    '''
    Arguments:
    prime_seq - priming sequence (converted t)
    predict_len - number of notes to predict for after prime sequence
    '''
    hidden = net.init_hidden()

    predicted = prime_seq.copy()
    prime_seq = torch.tensor(prime_seq, dtype = torch.long).to(device)


    # "Building up" the hidden state using the prime sequence
    for p in range(len(prime_seq) - 1):
        input = prime_seq[p]
        _, hidden = net(input, hidden)
    
    # Last character of prime sequence
    input = prime_seq[-1]
    
    # For every index to predict
    for p in range(predict_len):

        # Pass the inputs to the model - output has dimension n_pitches - scores for each of the possible characters
        output, hidden = net(input, hidden)
        # Sample from the network output as a multinomial distribution
        output = output.data.view(-1).div(temperature).exp()
        predicted_id = torch.multinomial(output, 1)

        # Add predicted index to the list and use as next input
        predicted.append(predicted_id.item()) 
        input = predicted_id

    return predicted

In [5]:
file_path = '/home/dmytro/ucu/music-generation/model.pkl'
with open(file_path, 'rb') as f:
    model = pickle.load(f)

In [6]:
file_path = '/home/dmytro/ucu/music-generation/int_to_note.pkl'
with open(file_path, 'rb') as f:
    int_to_note = pickle.load(f)

In [12]:
def create_midi(prediction_output):
    """ convert the output from the prediction to notes and create a midi file
        from the notes """
    offset = 0
    output_notes = []

    # create note and chord objects based on the values generated by the model
    for pattern in prediction_output:
        # pattern is a chord
        if ('.' in pattern) or pattern.isdigit():
            notes_in_chord = pattern.split('.')
            notes = []
            for current_note in notes_in_chord:
                new_note = note.Note(int(current_note))
                new_note.storedInstrument = instrument.Piano()
                notes.append(new_note)
            new_chord = chord.Chord(notes)
            new_chord.offset = offset
            output_notes.append(new_chord)
        # pattern is a note
        else:
            new_note = note.Note(pattern)
            new_note.offset = offset
            new_note.storedInstrument = instrument.Piano()
            output_notes.append(new_note)

        # increase offset each iteration so that notes do not stack
        offset += 0.5

    midi_stream = stream.Stream(output_notes)

    return midi_stream

In [30]:
input_melody = [727,
 224,
 55,
 55,
 727,
 224,
 55]


In [28]:
generated_seq_multinomial = predict_multimomial(model, input_melody, predict_len = 100, temperature = 2.2)
generated_seq_multinomial = [int_to_note[e] for e in generated_seq_multinomial]
pred_midi_multinomial = create_midi(generated_seq_multinomial)

In [29]:
pred_midi_multinomial.write('midi', fp='result.mid')

'/home/dmytro/ucu/music-generation/output/new_2.mid'

In [ ]:
sound_font = "/usr/share/sounds/sf2/FluidR3_GM.sf2"
FluidSynth(sound_font).midi_to_audio('result.midi', 'result.wav')
return 'result.wav', 'result.midi'

In [ ]:
def process_input():
    pass

In [ ]:
midi_file_desc = """Please entUpload your own MIDI file here (try to keep it small).
If you do not have a MIDI file, add some text and we will turn it into music!
"""

article = """# Pop Music Transformer
We are using a language model to create music by treating a musical standard MIDI a simple text, with tokens for note values, note duration, and separations to denote movement forward in time.

This is all following the great work you can find [at this repo](https://github.com/bearpelican/musicautobot). Moreover check out [their full web app](http://musicautobot.com/). We use the pretrained model they created as well as the utilities for converting between MIDI, audio streams, numpy encodings, and WAV files.

## Sonification

This is the process of turning something not inherently musical into music. Here we do something pretty simple. We take your input text "pretty cool", get a sentiment score (hard coded right now, model TODO), and use a major progression if it's positive and a minor progression if it's negative, and then factor the score into the randomness of the generated music. We also take the text and extract a melody by taking any of the letters from A to G, which in the example is just "E C". With the simple "E C" melody and a major progression a musical idea is generated.
"""

iface = gr.Interface(
    fn=process_input, 
    inputs=[
        gr.inputs.File(optional=True, label=midi_file_desc),
        "text", 
        gr.inputs.Slider(0, 250, default=100, step=50),
        gr.inputs.Radio([100, 200, 500], type="value", default=100)
        ], 
    outputs=["audio", "file"],
    article=article
    # examples=['C major scale.midi']
)

iface.launch()